In [1]:
import numpy as np
import pickle
# from Utils.TimeLogger import log
from scipy.sparse import csr_matrix
import time
import scipy.sparse as sp
minn = 1647180684
maxx = 0
import json
year_dict=dict()
def ok(year,month):
    global year_dict
    year_dict[year]=1
    if year == 2019:
        return True
    else:
        return False
def transTime(date):
    timeArr = time.strptime(date, '%Y-%m-%d %H:%M:%S')
    year = time.mktime(timeArr)
    global minn
    global maxx
    # global minn_y
    # global maxx_y
    # minn_y = min(minn_y,timeArr.tm_year)
    # maxx_y = max(maxx_y,timeArr.tm_year)

    if(ok(timeArr.tm_year,timeArr.tm_mon)):
        minn = min(minn, year)
        maxx = max(maxx, year)        
        return year
    return None# time.mktime(timeArr)

In [2]:
def mapping(infile):
    usrId = dict()
    itmId = dict()
    usrid, itmid = [0, 0]
    interaction = list()
    with open(infile, 'r', encoding='utf-8') as fs:
        for line in fs:
            data = json.loads(line.strip())
            row = data['user_id']
            col = data['business_id']
            timeStamp = transTime(data['date'])
            if(timeStamp==None):
                continue
            if row not in usrId:
                usrId[row] = usrid
                interaction.append(dict())
                usrid += 1
            if col not in itmId:
                itmId[col] = itmid
                itmid += 1
            usr = usrId[row]
            itm = itmId[col]
            if(itm not in interaction[usr]):
                interaction[usr][itm]=[]
            interaction[usr][itm].extend([timeStamp])
            '''
            if(len(interaction)>1000000):
                break
            '''
    print(minn, maxx,len(interaction))
    
    return interaction, usrid, itmid

In [3]:
def checkFunc1(cnt):
	return cnt >= 10
def checkFunc2(cnt):
	return cnt >= 5
def checkFunc3(cnt):
	return cnt >= 5

def filter(interaction, usrnum, itmnum, ucheckFunc, icheckFunc, filterItem=True):
    # get keep set
    usrKeep = set()
    itmKeep = set()
    itmCnt = [0] * itmnum
    for usr in range(usrnum):
        data = interaction[usr]
        usrCnt = 0
        for col in data:
            itmCnt[col] += 1
            usrCnt += 1
        if ucheckFunc(usrCnt):
            usrKeep.add(usr)
    for itm in range(itmnum):
        if not filterItem or icheckFunc(itmCnt[itm]):
            itmKeep.add(itm)

    # filter data
    retint = list()
    usrid = 0
    itmid = 0
    itmId = dict()
    user_id = list()
    item_id = list()
    time_int = list()
    for row in range(usrnum):
        if row not in usrKeep:
            continue
        usr = usrid
        usrid += 1
        retint.append(dict())
        data = interaction[row]
        for col in data:
            if col not in itmKeep:
                continue
            if col not in itmId:
                itmId[col] = itmid
                itmid += 1
            itm = itmId[col]
            retint[usr][itm] = data[col]
            for time_div in data[col]:
                user_id.append(usr+1)
                item_id.append(itm+1)
                time_int.append(int(time_div))
    return retint, usrid, itmid, user_id, item_id, time_int

In [4]:
def negSamp(temLabel, sampSize, nodeNum):
    negset = [None] * sampSize
    cur = 0
    while cur < sampSize:
        rdmItm = np.random.choice(nodeNum)
        if rdmItm not in temLabel:
            negset[cur] = rdmItm+1
            cur += 1
    return negset

def split(interaction, usrnum, itmnum):
    np.random.seed(100)
    pickNum = 10000
    # random pick
    usrPerm = np.random.permutation(usrnum)
    pickUsr = usrPerm[:pickNum]

    tstInt = [None] * usrnum
    trainPos = [None]* usrnum
    exception = 0
    user_id=list()
    item_id=list()
    time_id=list()
    neg_items=list()
    for usr in pickUsr:
        temp = list()
        data = interaction[usr]
        for itm in data:
            if (itm is not None and data[itm] is not None):
                temp.append((itm, data[itm]))
        if len(temp) == 0:
            print(usr)
            exception += 1
            continue
        # print('1',temp)
        temp.sort(key=lambda x: x[1])
        tstInt[usr] = temp[-1][0]
        # user_id.append(usr+1)
        # item_id.append(tstInt[usr]+1)
        # time_id.append(int(interaction[usr][tstInt[usr]][-1]))
        # neg_items.append(negSamp(interaction[usr],99,itmnum))
        interaction[usr][tstInt[usr]] = None
    user_behavior_sequence=list()
    for usr in range(usrnum):
        temp = list()
        data = interaction[usr]
        for itm in data:
            if(itm is not None and data[itm] is not None):
                temp.append((itm, data[itm]))
        if len(temp) == 0:
            print('2',usr)
            exception += 1
            continue
        #print(temp)
        temp.sort(key=lambda x: x[1])
        user_behavior_sequence.append(np.array(temp)[:-1,0])
        trainPos[usr] = temp[-1][0]
        interaction[usr][temp[-1][0]] = None
    print(user_id,time_id,time_id,neg_items)
    # train=DataFrame({'user_id':user_id, 'item_id':item_id, 'time':time_id, 'neg_items':neg_items})
    # train.to_csv('test_yelp_4.csv',index=False,sep='\t')
    # print(train)
    print('Exception:', exception, np.sum(np.array(tstInt)!=None))
    return interaction, tstInt, trainPos, user_behavior_sequence

In [5]:
from pandas.core.frame import DataFrame
prefix = 'D:/edgedownload/'
print('Start')
minn = 1647180684
maxx = 0
minn_y = 2022
maxx_y = 2000
interaction, usrnum, itmnum = mapping(prefix + 'yelp_review')
print('Id Mapped, usr %d, itm %d' % (usrnum, itmnum))

Start
1546272009.0 1576223479.0 545233
Id Mapped, usr 545233, itm 128228


In [6]:
maxx

1576223479.0

In [96]:
year_dict

{2015: 1,
 2013: 1,
 2011: 1,
 2017: 1,
 2009: 1,
 2016: 1,
 2018: 1,
 2010: 1,
 2014: 1,
 2012: 1,
 2005: 1,
 2007: 1,
 2008: 1,
 2006: 1,
 2019: 1,
 2004: 1}

In [6]:
checkFuncs = [checkFunc1, checkFunc2, checkFunc3]
for i in range(3):
    filterItem = True if i < 1 else False
    interaction, usrnum, itmnum, user_id, item_id, time_int = filter(interaction, usrnum, itmnum, checkFuncs[i], checkFuncs[i], filterItem)
    print('Filter', i, 'times:', usrnum, itmnum)
    '''
    if(i==2):
        train=DataFrame({'user_id':user_id, 'item_id':item_id, 'time':time_int})
        train.to_csv('train_yelp.csv',index=False,sep='\t')
        print(train)
    '''
        
print('Sparse Samples Filtered, usr %d, itm %d' % (usrnum, itmnum))


Filter 0 times: 13501 24682
Filter 1 times: 13094 24634
Filter 2 times: 13094 24634
Sparse Samples Filtered, usr 13094, itm 24634


In [178]:
train['eventdate']=pd.to_datetime(train['time'],unit='s')

In [15]:
def count_frequency(interaction,usernum,itmnum):
    count_item=np.zeros([itmnum],dtype=int)
    for i in range(itmnum):
        for j in range(usernum):
            if(i in interaction[j] and interaction[j][i] is not None):
                count_item[i]+=len(interaction[j][i])
    print(count_item)
    return np.argsort(count_item)

In [42]:
interaction[0][1]

[1553012198.0]

In [16]:
ret=count_frequency(interaction,usrnum,itmnum)

[38  4  7 ...  1  1  1]


In [17]:
ret[-100:]

array([3920,  796, 1516, 2498, 1538, 2375, 5931, 5548, 3959, 3665, 2934,
       1053,  378,  594,   98,  596, 5962, 2449, 1556, 8812, 2825, 1171,
       2586,  425, 3072, 4359,  209, 2478, 2628, 2752, 2126, 1130, 1501,
       4145, 1778,  962, 6674, 1774, 1042, 4108, 2162, 2923, 2435,  619,
        634,  584, 1496, 1385, 1854,  728,  147, 3352, 2124, 1702, 2240,
       1559, 2379, 1266,  674, 2853, 1068,  585, 1107,  557,  718, 1957,
       2313, 1795, 1639,  389, 5867, 1071, 5961, 2310, 1510,  583,  629,
       1535,  741,  589, 1100, 1506,  571, 1138, 1497, 2242, 1563, 4402,
        523,   97, 1716, 2386, 2675, 2562,  387,  972,  609, 2419, 1267,
        595], dtype=int64)

In [19]:
neg_frequency=ret

In [20]:
with open(prefix+'yelp_sort825', 'wb') as fs:
	pickle.dump(neg_frequency, fs)

In [16]:
with open(prefix+'yelp_sort2', 'rb') as fs:
    negfrequency = pickle.load(fs)

In [51]:
neg_frequency.max()

24633

In [103]:
def negSamp_fre(temLabel, sampSize, nodeNum):
    negset = [None] * sampSize
    cur = 0
    i = 0
    while cur < sampSize:
        rdmItm = neg_frequency[-i]# np.random.choice(nodeNum)
        if rdmItm not in temLabel:
            negset[cur] = rdmItm+1
            cur += 1
        i += 1
    return negset

def split(interaction, usrnum, itmnum):
    np.random.seed(100)
    pickNum = 10000
    # random pick
    usrPerm = np.random.permutation(usrnum)
    pickUsr = usrPerm[:pickNum]

    tstInt = [None] * usrnum
    exception = 0
    user_id=list()
    item_id=list()
    time_id=list()
    neg_items=list()
    for usr in pickUsr:
        temp = list()
        data = interaction[usr]
        for itm in data:
            temp.append((itm, data[itm]))
        if len(temp) == 0:
            exception += 1
            continue
        temp.sort(key=lambda x: x[1])
        tstInt[usr] = temp[-1][0]
        user_id.append(usr+1)
        item_id.append(tstInt[usr]+1)
        time_id.append(int(interaction[usr][tstInt[usr]][-1]))
        neg_items.append(negSamp_fre(interaction[usr],99,itmnum))
        interaction[usr][tstInt[usr]] = None
    print(user_id,time_id,time_id,neg_items)
    train=DataFrame({'user_id':user_id, 'item_id':item_id, 'time':time_id, 'neg_items':neg_items})
    train.to_csv('test_amazon.csv',index=False,sep='\t')
    print(train)
    print('Exception:', exception, np.sum(np.array(tstInt)!=None))
    return interaction, tstInt

In [8]:
year_count={2004:0,2005:0,2006:0,2007:0,2008:0,2009:0,2010:0,2011:0,2012:0,2014:0,2015:0,2016:0,2017:0,2018:0,2019:0}
timelist=train['eventdate'].values
dates = pd.DatetimeIndex(train['eventdate'].values)
for i in range(len(timelist)):
    year_count[dates[i].year]+=1

KeyError: 'eventdate'

In [180]:
year_count

{2004: 0,
 2005: 0,
 2006: 0,
 2007: 0,
 2008: 0,
 2009: 0,
 2010: 0,
 2011: 0,
 2012: 0,
 2014: 0,
 2015: 0,
 2016: 0,
 2017: 258,
 2018: 337384,
 2019: 153771}

In [7]:
def trans_sub(interaction, usrnum, itmnum, gragh_num):
	global minn
	global maxx
	interval = (maxx-minn)/gragh_num
	rcd = [[list(), list(), list()]]
	for i in range(gragh_num-1):
		rcd.append([list(), list(), list()])
	timeMat = sp.dok_matrix((usrnum, itmnum), dtype=np.int)
	for usr in range(usrnum):
		if interaction[usr] == None:
			continue
		data = interaction[usr]
		for col in data:
			if data[col] != None:
				for one_data in data[col]:
					gragh_no=int(((one_data-minn)/interval))
					if(gragh_no>=gragh_num):
						print(one_data,gragh_no)
						gragh_no=gragh_num-1
					# print(gragh_no,one_data)
					if(len(rcd[gragh_no][0])==0 or  rcd[gragh_no][0][-1]!=usr or rcd[gragh_no][1][-1]!=col):
						rcd[gragh_no][0].append(usr)
						rcd[gragh_no][1].append(col)
						rcd[gragh_no][2].append(one_data)
						# rcd[gragh_no][0].append(usrnum+col)
						# rcd[gragh_no][1].append(usr)
						# rcd[gragh_no][2].append(1.0)
						timeMat[usr,col]=gragh_no
	intMat=list()
	for i in range(gragh_num):
		intMat.append(csr_matrix((rcd[i][2], (rcd[i][0], rcd[i][1])), shape=(usrnum, itmnum)))
		# intMat.append(normalized_adj_single(csr_matrix((rcd[i][2], (rcd[i][0], rcd[i][1])), shape=(usrnum+itmnum, usrnum+itmnum))))+itmnum usrnum+
		print(intMat[i])
	return intMat, timeMat.tocsr()

In [8]:
# print(interaction, usrnum, itmnum), trainPos
trnInt, tstInt, trainPos, user_behavior_sequence = split(interaction, usrnum, itmnum)
print('Datasets Splited')


[] [] [] []
Exception: 0 10000
Datasets Splited


C:\Users\LIU-YUXI\AppData\Local\Temp/ipykernel_20416/2224593916.py:56: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  user_behavior_sequence.append(np.array(temp)[:-1,0])


In [14]:
def transtocsv(interaction, usrnum, itmnum):
    user_id = list()
    item_id = list()
    time_int = list()
    for row in range(usrnum):
        data = interaction[row]
        print(data)
        for col in data:
            # print(col)
            if(data[col] is None):
                continue
            for time_div in data[col]:
                user_id.append(row+1)
                item_id.append(col+1)
                time_int.append(int(time_div))
    return user_id,item_id,time_int
user_id, item_id, time_int = transtocsv(interaction, usrnum, itmnum)
train=DataFrame({'user_id':user_id, 'item_id':item_id, 'time':time_int})
train.to_csv('train_yelp.csv',index=False,sep='\t')

{0: [1546427509.0], 1: [1553012198.0], 2: [1547818381.0], 3: None, 4: [1560428434.0], 5: [1558793506.0], 6: [1565266433.0], 7: [1561321017.0], 8: [1562410176.0], 9: [1561640204.0], 10: [1558979339.0], 11: [1561707588.0], 12: [1565276162.0], 13: [1566811331.0], 14: [1571048723.0], 15: [1559575279.0], 16: [1548088191.0], 17: [1557572519.0], 18: [1546968178.0], 19: [1562418928.0], 20: [1555239172.0, 1552548834.0], 21: [1553104732.0], 22: [1558529298.0], 23: [1561151628.0], 24: [1555778423.0], 25: [1563792323.0], 26: [1550389124.0], 27: [1563060914.0], 28: [1571445190.0], 29: None, 30: [1563386128.0], 31: [1549735247.0], 32: [1557389303.0], 33: [1560098689.0], 34: [1562673807.0], 35: [1546523058.0, 1549123732.0, 1546967959.0, 1570894260.0], 36: [1561537313.0], 37: [1550572983.0], 38: [1557569472.0], 39: [1559040976.0], 40: [1568109138.0], 41: [1549793075.0, 1568108924.0], 42: [1558170836.0], 43: [1559575126.0], 44: [1556971145.0], 45: [1554051170.0], 46: [1555096881.0], 47: [1555605885.0],

In [ ]:
print(trainPos)

In [11]:
print(user_behavior_sequence[0])

[5 3 0 2 1 9 7 6 8]


In [10]:
tstInt

[6,
 11,
 None,
 61,
 None,
 104,
 None,
 None,
 160,
 None,
 210,
 229,
 232,
 241,
 None,
 374,
 404,
 None,
 None,
 439,
 466,
 472,
 495,
 522,
 None,
 246,
 None,
 None,
 None,
 694,
 702,
 712,
 None,
 None,
 743,
 778,
 781,
 None,
 None,
 None,
 None,
 1010,
 1053,
 1101,
 None,
 None,
 1143,
 1147,
 None,
 1199,
 1214,
 1218,
 1316,
 None,
 1385,
 1441,
 1451,
 1484,
 755,
 1546,
 None,
 1557,
 None,
 None,
 1640,
 1649,
 1666,
 1689,
 1699,
 1824,
 None,
 None,
 None,
 1866,
 1104,
 1927,
 748,
 1840,
 None,
 None,
 2004,
 2047,
 2057,
 None,
 2089,
 2129,
 47,
 None,
 2237,
 None,
 None,
 2295,
 2313,
 2336,
 1998,
 None,
 2422,
 2446,
 None,
 None,
 None,
 None,
 2495,
 1341,
 548,
 None,
 None,
 2599,
 2601,
 None,
 None,
 None,
 None,
 2693,
 None,
 2718,
 2520,
 2733,
 None,
 2800,
 None,
 2842,
 None,
 None,
 49,
 None,
 2902,
 2144,
 2952,
 2957,
 2969,
 2990,
 None,
 1349,
 3018,
 3031,
 None,
 None,
 3068,
 3076,
 3086,
 3096,
 3141,
 None,
 3185,
 3189,
 None,
 None

In [12]:
with open(prefix+'train_pos_yelp', 'wb') as fs:
	pickle.dump(trainPos, fs)

In [13]:
with open(prefix+'tst_intyelp', 'wb') as fs:
	pickle.dump(tstInt, fs)

In [31]:
with open(prefix+'tstInt4', 'rb') as fs:
	tst_Int=pickle.load(fs)

EOFError: Ran out of input

In [32]:
tstInt

[None,
 None,
 None,
 None,
 None,
 175,
 198,
 None,
 226,
 None,
 None,
 None,
 278,
 None,
 None,
 None,
 432,
 None,
 None,
 None,
 None,
 None,
 None,
 747,
 None,
 None,
 804,
 None,
 None,
 865,
 None,
 989,
 None,
 1094,
 1104,
 None,
 1202,
 None,
 1234,
 None,
 None,
 None,
 None,
 1305,
 None,
 None,
 None,
 None,
 None,
 1730,
 1736,
 None,
 1771,
 1796,
 1857,
 None,
 None,
 1877,
 None,
 None,
 2009,
 None,
 None,
 None,
 2116,
 None,
 None,
 None,
 None,
 None,
 None,
 229,
 None,
 2594,
 171,
 None,
 2653,
 None,
 2712,
 None,
 None,
 2764,
 None,
 None,
 None,
 2878,
 555,
 None,
 None,
 None,
 None,
 3143,
 3168,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 3392,
 None,
 None,
 None,
 None,
 None,
 None,
 3566,
 None,
 None,
 None,
 None,
 None,
 None,
 3957,
 90,
 None,
 158,
 None,
 None,
 None,
 None,
 None,
 4139,
 4157,
 None,
 None,
 None,
 None,
 None,
 None,
 4326,
 4344,
 None,
 None,
 None,
 None,
 4421,
 4454,
 4465,
 None,
 4508,
 None,
 4553,


In [9]:
minn = 1647180684
maxx = 0
def trans(interaction, usrnum, itmnum):
	global maxx,minn
	r, c, d = [list(), list(), list()]
	for usr in range(usrnum):
		if interaction[usr] == None:
			continue
		data = interaction[usr]
		for col in data:
			if data[col] != None:
				for one_data in data[col]:
					if(one_data>maxx):
						maxx=one_data
					if(one_data<minn):
						minn=one_data
					r.append(usr)
					c.append(col)
					d.append(1.0)
	print(max(r),max(c))
	intMat = csr_matrix((d, (r, c)), shape=(usrnum, itmnum))
	return intMat

In [21]:
print(usrnum,itmnum)
trnMat = [trans(trnInt, usrnum, itmnum)]
print(maxx,minn)
subMat,timeMat=trans_sub(trnInt, usrnum, itmnum, 14)
print(timeMat)
trnMat.append(subMat)
trnMat.append(timeMat)
print('Train Mat Done')
with open(prefix+'trn_mat_time_yelp', 'wb') as fs:
	pickle.dump(trnMat, fs)

13094 24634
13093 24633
1576218919.0 1546272009.0


C:\Users\LIU-YUXI\AppData\Local\Temp/ipykernel_20416/2970320320.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  timeMat = sp.dok_matrix((usrnum, itmnum), dtype=np.int)


1576218919.0 14
  (0, 0)	1546427509.0
  (0, 2)	1547818381.0
  (0, 16)	1548088191.0
  (0, 18)	1546968178.0
  (0, 35)	1546523058.0
  (0, 53)	1546522959.0
  (0, 57)	1546870047.0
  (1, 61)	1548247915.0
  (1, 62)	1548249510.0
  (1, 63)	1548248554.0
  (1, 66)	1548248321.0
  (2, 67)	1547329759.0
  (2, 75)	1546527984.0
  (3, 78)	1548009632.0
  (4, 90)	1547988708.0
  (5, 104)	1546775678.0
  (5, 110)	1546588992.0
  (6, 116)	1547939792.0
  (6, 124)	1548357409.0
  (6, 125)	1546934296.0
  (6, 137)	1548198302.0
  (6, 145)	1546384529.0
  (6, 146)	1547235641.0
  (6, 150)	1547120457.0
  (6, 156)	1547418791.0
  :	:
  (13070, 8974)	1546520100.0
  (13070, 15102)	1546519062.0
  (13070, 15393)	1546519932.0
  (13070, 15474)	1546519797.0
  (13070, 16444)	1546519426.0
  (13070, 17571)	1546520196.0
  (13070, 20421)	1546519286.0
  (13071, 3297)	1547874740.0
  (13071, 14203)	1547873866.0
  (13072, 3268)	1547604907.0
  (13074, 5492)	1547226797.0
  (13074, 18909)	1547109692.0
  (13074, 19967)	1548003797.0
  (13081,

In [11]:
trnMat

[<13094x24634 sparse matrix of type '<class 'numpy.float64'>'
 	with 185590 stored elements in Compressed Sparse Row format>,
 [<13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 18049 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 18278 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 18167 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 18072 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 17442 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 17349 stored elements in Compressed Sparse Row format>,
  <13094x24634 sparse matrix of type '<class 'numpy.float64'>'
  	with 17983 stored elements in Compressed Spars

In [34]:
yelp_sequence=list()
for i in range(len(user_behavior_sequence)):
    indexs=np.array(range(len(user_behavior_sequence[i])))
    indexs=np.expand_dims(indexs,axis=1)
    
    yelp_sequence.append(np.concatenate((indexs,np.expand_dims(user_behavior_sequence[i],axis=1)),axis=1))

In [40]:
np.random.choice(yelp_sequence[0],5)

ValueError: a must be 1-dimensional

In [10]:
with open(prefix+'yelp_sequence', 'wb') as fs:
	pickle.dump(user_behavior_sequence, fs)

In [23]:
print(trnMat[0][0],trnMat[1][0])

  (0, 0)	1.0
  (0, 1)	1.0
  (0, 2)	1.0
  (0, 3)	1.0
  (0, 4)	1.0
  (0, 5)	1.0
  (0, 6)	1.0
  (0, 7)	1.0
  (0, 8)	2.0
  (0, 9)	1.0   (0, 34306)	1.0
  (0, 34307)	1.0
  (0, 34308)	1.0
  (0, 34309)	1.0
  (0, 34311)	1.0
  (0, 34313)	1.0
  (0, 34314)	1.0
  (0, 34315)	1.0
  (1, 34320)	1.0
  (1, 34321)	1.0
  (1, 34326)	1.0
  (2, 34327)	1.0
  (2, 34331)	1.0
  (2, 34337)	1.0
  (2, 34342)	1.0
  (2, 34346)	1.0
  (3, 34367)	1.0
  (3, 34369)	1.0
  (3, 34370)	1.0
  (3, 34372)	1.0
  (3, 34376)	1.0
  (3, 34378)	1.0
  (3, 34386)	1.0
  (3, 34396)	1.0
  (3, 34409)	1.0
  :	:
  (80280, 33393)	1.0
  (80282, 32716)	1.0
  (80287, 32812)	1.0
  (80291, 32853)	2.0
  (80291, 33050)	2.0
  (80293, 32862)	1.0
  (80302, 33141)	1.0
  (80303, 33142)	1.0
  (80306, 33163)	1.0
  (80307, 33173)	1.0
  (80309, 33197)	2.0
  (80310, 33206)	1.0
  (80311, 33956)	2.0
  (80313, 33229)	1.0
  (80317, 33314)	1.0
  (80319, 33331)	1.0
  (80321, 33354)	1.0
  (80328, 33399)	1.0
  (80336, 33535)	1.0
  (80338, 33576)	1.0
  (80350, 33781)	1.

In [24]:
print(interaction[0])

{0: [1523761991.0], 1: [1525066214.0], 2: [1524846617.0], 3: [1523761085.0], 4: [1547526623.0], 5: [1518001321.0], 6: [1542267536.0], 7: [1528378033.0], 8: [1542459237.0, 1517644608.0], 9: [1525066342.0]}


In [15]:
import pandas as pd
train=pd.read_csv('train_yelp_.csv',sep='\t')
train

user_id  item_id        time
0             1        1  1523761991
1             1        2  1525066214
2             1        3  1524846617
3             1        4  1523761085
4             1        5  1547526623
...         ...      ...         ...
705951    34306    40667  1573242865
705952    34306     1208  1550080613
705953    34306     4345  1555269795
705954    34306     9853  1522519777
705955    34306      265  1571595313

[705956 rows x 3 columns]

In [15]:
trnMat

[<34306x46069 sparse matrix of type '<class 'numpy.float64'>'
 	with 666793 stored elements in Compressed Sparse Row format>,
 [<80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 231482 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 121526 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 126076 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 112160 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 107806 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 110046 stored elements in Compressed Sparse Row format>,
  <80375x80375 sparse matrix of type '<class 'numpy.float64'>'
  	with 114986 stored elements in Compresse

In [16]:
maxx=train.time.max()
minn=train.time.min()

In [17]:
df_clear = train.drop(train[(train['user_id']==test.user_id[0]) &(train['item_id']==test.item_id[0]) ].index)

NameError: name 'test' is not defined

In [17]:
df_clear[df_clear.user_id==test.user_id[0]]


user_id  item_id        time
1612866    34960    34960  1286871673
1612867    34960    34960  1282032218
1612868    34960     9286  1286635582
1612869    34960     9286  1281805086
1612870    34960    44839  1286612235
...          ...      ...         ...
1612947    34960     9137  1272089125
1612948    34960    15587  1272011303
1612949    34960    22871  1271247631
1612950    34960    55664  1270805475
1612951    34960     9325  1270317390

[86 rows x 3 columns]

In [20]:
len(train[(train['user_id']==test.user_id[0]) &(train['item_id']==test.item_id[0]) ])

34

In [21]:
for i in range(1,10000):
    # print(test.item_id[i],test.user_id[i])
    df_clear.drop(df_clear[(df_clear['user_id']==test.user_id[i]) &(df_clear['item_id']==test.item_id[i]) ].index,inplace=True)

In [47]:
import pandas as pd
test=pd.read_csv('D:/edgedownload/yelp_review',sep='\t')
test

{"review_id":"xQY8N_XvtGbearJ5X4QryQ","user_id":"OwjRMXRC0KyPrIlcjaXeFQ","business_id":"-MhfebM0QIsKt87iDN-FNw","stars":2.0,"useful":5,"funny":0,"cool":0,"text":"As someone who has worked with many museums, I was eager to visit this gallery on my most recent trip to Las Vegas. When I saw they would be showing infamous eggs of the House of Faberge from the Virginia Museum of Fine Arts (VMFA), I knew I had to go!\n\nTucked away near the gelateria and the garden, the Gallery is pretty much hidden from view. It's what real estate agents would call \"cozy\" or \"charming\" - basically any euphemism for small.\n\nThat being said, you can still see wonderful art at a gallery of any size, so why the two *s you ask? Let me tell you:\n\n* pricing for this, while relatively inexpensive for a Las Vegas attraction, is completely over the top. For the space and the amount of art you can fit in there, it is a bit much.\n* it's not kid friendly at all. Seriously, don't bring them.\n* the security is not trained properly for the show. When the curating and design teams collaborate for exhibitions, there is a definite flow. That means visitors should view the art in a certain sequence, whether it be by historical period or cultural significance (this is how audio guides are usually developed). When I arrived in the gallery I could not tell where to start, and security was certainly not helpful. I was told to \"just look around\" and \"do whatever.\" \n\nAt such a *fine* institution, I find the lack of knowledge and respect for the art appalling.","date":"2015-04-15 05:21:16"}
0        {"review_id":"UmFMZ8PyXZTY2QcwzsfQYA","user_id...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
1        {"review_id":"LG2ZaYiOgpr2DK_90pYjNw","user_id...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [26]:
df_clear[df_clear.user_id==4866]

user_id  item_id        time
529152     4866     3933  1265998360
529153     4866    34896  1264625094
529154     4866     4987  1264423076
529155     4866     4987  1262953642
529156     4866    13282  1263838812
529157     4866    21143  1263754681
529158     4866     1711  1263578895
529159     4866     8166  1263557967
529160     4866     8123  1263318153
529161     4866    21137  1263062928
529162     4866    34899  1262593453
529163     4866    12042  1262179195
529164     4866    39049  1262004554
529165     4866     8211  1261848788
529166     4866    23934  1261821706

In [27]:
train[train.user_id==4866]

user_id  item_id        time
529151     4866    36665  1279044340
529152     4866     3933  1265998360
529153     4866    34896  1264625094
529154     4866     4987  1264423076
529155     4866     4987  1262953642
529156     4866    13282  1263838812
529157     4866    21143  1263754681
529158     4866     1711  1263578895
529159     4866     8166  1263557967
529160     4866     8123  1263318153
529161     4866    21137  1263062928
529162     4866    34899  1262593453
529163     4866    12042  1262179195
529164     4866    39049  1262004554
529165     4866     8211  1261848788
529166     4866    23934  1261821706

In [24]:
df_clear.to_csv('train_gowalla_srgnn.csv',index=False,sep='\t')

In [2]:
import pickle
train_data = pickle.load(open('D:/experiment/SR-GNN-master/datasets/yoo/train.txt', 'rb'))

In [5]:
maxxx=0
for i in range(len(train_data[0])):
    # print(len(train_data[0][i]))
    maxxx=max(maxxx,len(train_data[0][i]))
maxxx

145

In [6]:
len(train_data[0])

369859

In [46]:
train_data2 = pickle.load(open('D:/edgedownload/yelp_review', 'rb'))

UnpicklingError: invalid load key, '{'.

In [10]:
maxxx=0
for i in range(len(train_data2[0])):
    # print(len(train_data[0][i]))
    maxxx=max(maxxx,len(train_data2[0][i]))
maxxx

942

In [11]:
len(train_data2[0])

37705

In [80]:
import pandas as pd
train=pd.read_csv('D:\experiment\ReChorus-master\data\yelp_lyx\\train.csv',sep='\t')
train

user_id  item_id        time
0             1        1  1523761991
1             1        2  1525066214
2             1        3  1524846617
3             1        4  1523761085
4             1        5  1547526623
...         ...      ...         ...
705951    34306    40667  1573242865
705952    34306     1208  1550080613
705953    34306     4345  1555269795
705954    34306     9853  1522519777
705955    34306      265  1571595313

[705956 rows x 3 columns]

In [81]:
train['rank']=0

In [82]:
order = ['user_id','item_id','rank','time']
train = train[order]

In [83]:
train.to_csv('D:\experiment\BPR-pytorch-master\\yelp_train.csv',header=False,index=False,sep='\t')

In [33]:
import pandas as pd
test=pd.read_csv('D:\experiment\ReChorus-master\data\yelp_lyx\\test.csv',sep='\t')
test['rank']=1
order = ['user_id','item_id','rank','time']
test = test[order]

In [34]:
test.to_csv('D:\experiment\BPR-pytorch-master\\yelp_test.csv',header=False,index=False,sep='\t')

In [35]:
test

user_id  item_id  rank        time
0       11040    22103     1  1545837432
1       12764    39304     1  1557328121
2        8208    39295     1  1570206193
3       13241     8541     1  1558630213
4        7240    27618     1  1568653123
...       ...      ...   ...         ...
9995    18959     1283     1  1560463372
9996    26311    35552     1  1568209261
9997     3741    19849     1  1575286459
9998    15113     2372     1  1545174020
9999    32959    37607     1  1568583110

[10000 rows x 4 columns]

In [36]:
test=pd.read_csv('D:\experiment\ReChorus-master\data\yelp_lyx\\test.csv',sep='\t')
test

user_id  item_id        time  \
0       11040    22103  1545837432   
1       12764    39304  1557328121   
2        8208    39295  1570206193   
3       13241     8541  1558630213   
4        7240    27618  1568653123   
...       ...      ...         ...   
9995    18959     1283  1560463372   
9996    26311    35552  1568209261   
9997     3741    19849  1575286459   
9998    15113     2372  1545174020   
9999    32959    37607  1568583110   

                                              neg_items  
0     [1033, 23373, 12631, 12370, 4171, 34796, 9768,...  
1     [32756, 36433, 41888, 704, 20229, 20581, 44406...  
2     [1175, 2497, 26460, 37239, 36388, 31994, 41459...  
3     [7622, 44543, 8886, 14560, 12781, 35074, 32090...  
4     [12564, 22232, 24876, 44077, 19289, 28218, 850...  
...                                                 ...  
9995  [45584, 21858, 23032, 3020, 15935, 5193, 9281,...  
9996  [17464, 36117, 30526, 44296, 42412, 35172, 399...  
9997  [29888, 39760, 17405, 3565, 2118, 5716, 38941,...  
9998  [39073, 20105, 11185, 3821, 45853, 34663, 1226...  
9999  [14790, 24001, 19850, 44063, 6159, 12876, 3837...  

[10000 rows x 4 columns]

In [41]:
test_neg=pd.DataFrame()
test_neg['1']=(test['user_id'],test['item_id'])

In [46]:
test_neg=pd.DataFrame()
test_neg['1']=list(zip(test['user_id'].values, test['item_id'].values))


In [47]:
test_neg

1
0     (11040, 22103)
1     (12764, 39304)
2      (8208, 39295)
3      (13241, 8541)
4      (7240, 27618)
...              ...
9995   (18959, 1283)
9996  (26311, 35552)
9997   (3741, 19849)
9998   (15113, 2372)
9999  (32959, 37607)

[10000 rows x 1 columns]

In [48]:
test_neg['2']=test.neg_items

In [49]:
test_neg

1                                                  2
0     (11040, 22103)  [1033, 23373, 12631, 12370, 4171, 34796, 9768,...
1     (12764, 39304)  [32756, 36433, 41888, 704, 20229, 20581, 44406...
2      (8208, 39295)  [1175, 2497, 26460, 37239, 36388, 31994, 41459...
3      (13241, 8541)  [7622, 44543, 8886, 14560, 12781, 35074, 32090...
4      (7240, 27618)  [12564, 22232, 24876, 44077, 19289, 28218, 850...
...              ...                                                ...
9995   (18959, 1283)  [45584, 21858, 23032, 3020, 15935, 5193, 9281,...
9996  (26311, 35552)  [17464, 36117, 30526, 44296, 42412, 35172, 399...
9997   (3741, 19849)  [29888, 39760, 17405, 3565, 2118, 5716, 38941,...
9998   (15113, 2372)  [39073, 20105, 11185, 3821, 45853, 34663, 1226...
9999  (32959, 37607)  [14790, 24001, 19850, 44063, 6159, 12876, 3837...

[10000 rows x 2 columns]

In [50]:
test_neg.to_csv('D:\experiment\BPR-pytorch-master\\yelp_test_neg.csv',header=False,index=False,sep='\t')

In [57]:
negs=np.concatenate(neg_list,axis=1)

AxisError: axis 1 is out of bounds for array of dimension 1

In [55]:
import ast
neg_list=[]
for i in range(10000):
    neg_list.append(ast.literal_eval(test.neg_items.values[i]))

In [56]:
neg_list

[[1033,
  23373,
  12631,
  12370,
  4171,
  34796,
  9768,
  20935,
  37258,
  44878,
  1589,
  6342,
  22517,
  5490,
  17631,
  39361,
  16931,
  44580,
  32160,
  13379,
  22161,
  22026,
  170,
  30958,
  26933,
  44106,
  21994,
  4998,
  23955,
  44986,
  31878,
  32910,
  37055,
  28877,
  8519,
  25504,
  39221,
  18587,
  17482,
  12541,
  16651,
  20505,
  26370,
  10224,
  33178,
  45512,
  43706,
  8681,
  24878,
  20329,
  35412,
  11042,
  6039,
  39478,
  3176,
  19316,
  16766,
  6127,
  32490,
  18260,
  8532,
  10711,
  5453,
  24688,
  3179,
  2049,
  8521,
  42667,
  41726,
  34085,
  26948,
  6238,
  26336,
  22842,
  5108,
  5226,
  23985,
  15825,
  42394,
  6287,
  13746,
  40837,
  11052,
  28381,
  32775,
  37465,
  38260,
  2749,
  5522,
  31422,
  26369,
  3071,
  44374,
  7058,
  11489,
  33694,
  31280,
  4449,
  16643],
 [32756,
  36433,
  41888,
  704,
  20229,
  20581,
  44406,
  12526,
  8970,
  17121,
  5923,
  30582,
  20222,
  3339,
  19385,
  4210

In [69]:
neg_list2=[]
for i in range(99):
    neg_list2.append(neg_list[:,i])

In [68]:
neg_list=np.array(neg_list)

In [73]:
neg_list2[1].shape

(10000,)

In [74]:
for i in range(99):
    test_neg['a'+str(i)]=neg_list2[i]


C:\Users\LIU-YUXI\AppData\Local\Temp/ipykernel_30144/164952036.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  test_neg['a'+str(i)]=neg_list2[i]


In [77]:
test_neg.drop(columns=['2'],inplace=True) 

In [79]:
test_neg.to_csv('D:\experiment\BPR-pytorch-master\\yelp_test_neg.csv',header=False,index=False,sep='\t')